In [12]:
#@title Imports and Utility Functions
from __future__ import absolute_import
from __future__ import division
from __future__ import print_function

import os
from collections import Counter
import gin
import json
import numpy as np
# import matplotlib.pyplot as plt
import tensorflow.compat.v1 as tf
from meta_dataset.data import config
from meta_dataset.data import dataset_spec as dataset_spec_lib
from meta_dataset.data import learning_spec
from meta_dataset.data import pipeline

# set seed for reproducibility
seed=1
tf.set_random_seed(seed)
np.random.seed(seed)

# enable eager mode
tf.enable_eager_execution()
# tf.disable_eager_execution()

In [13]:
!pip install tfrecord

In [19]:
import tfrecord

total_support, total_query = 0, 0
for class_id in range(125, 177):
    try:
        loader = tfrecord.tfrecord_loader(
            f"/home/jishnu/Documents/github/meta-dataset/records-non-oversampled/tesla-mixture/{class_id}.tfrecords", None, {
            "image": "byte",
            "label": "int",
            "set": "byte"
        })
        num_support, num_query = 0, 0
        for idx, record in enumerate(loader):
            len_set = len(record["set"])
            _set = ""
            if len_set == 7:
                _set = 'support'
                num_support+=1
            elif len_set == 5:
                _set = 'query'
                num_query+=1
            else:
                set = 'none'
        total_query += num_query
        total_support += num_support
        print(f"{class_id=} {num_support=}, {num_query}")
    except:
        pass
print(f"{total_support=}, {total_query=}")

class_id=125 num_support=27, 68
class_id=126 num_support=36, 112
class_id=127 num_support=18, 54
class_id=128 num_support=18, 34
class_id=129 num_support=18, 12
class_id=130 num_support=18, 26
class_id=131 num_support=45, 12
class_id=132 num_support=18, 36
class_id=133 num_support=36, 250
class_id=134 num_support=9, 38
class_id=135 num_support=18, 14
class_id=136 num_support=18, 18
class_id=137 num_support=18, 22
class_id=138 num_support=18, 18
class_id=139 num_support=9, 18
class_id=140 num_support=27, 102
class_id=141 num_support=9, 18
class_id=142 num_support=27, 37
class_id=143 num_support=9, 18
class_id=144 num_support=9, 26
class_id=145 num_support=18, 52
class_id=146 num_support=18, 48
class_id=147 num_support=18, 22
class_id=148 num_support=27, 40
class_id=149 num_support=18, 21
class_id=150 num_support=27, 104
class_id=151 num_support=45, 44
class_id=152 num_support=9, 16
class_id=153 num_support=18, 68
class_id=154 num_support=9, 48
class_id=155 num_support=18, 31
class_id=15

In [27]:
import json

with open("/home/jishnu/Documents/github/meta-dataset/records-non-oversampled/tesla-mixture/dataset_spec.json") as f:
    d = json.load(f)
    
total_support, total_query = 0, 0
for class_id in range(125, 177):
    class_id= str(class_id)
    total_support += d['images_per_class'][class_id]['support']
    total_query += d['images_per_class'][class_id]['query']

total_support, total_query

(1026, 2296)

In [33]:
import os

parent_dir = "/home/jishnu/Desktop/TESLA/test_data"

total_classes_with_query=0
total_query = 0
for class_dir_name in os.listdir(parent_dir):
    class_dir_path = os.path.join(parent_dir, class_dir_name)
    if "query" in os.listdir(class_dir_path):
        total_classes_with_query += 1
        current_query_set_size = len(os.listdir(os.path.join(class_dir_path, "query")))
        total_query += current_query_set_size
        print(f"{class_dir_name}: {current_query_set_size}")
print(f"{total_classes_with_query=} {total_query=}")

sponge: 80
bell_pepper: 12
cereal_box: 250
tomato: 19
football: 18
instant_noodle_packet: 26
stapler: 28
mustard_bottle: 16
orange: 68
towel: 60
bulb_box: 36
binder: 26
pringles_can: 24
wood_box: 22
timer: 22
pear: 31
baseball_ball: 34
lemon: 40
ball: 112
soft_scrub_cleanser_bottle: 16
soda_can: 76
power_drill: 16
cracker_box: 22
apple: 68
marker: 104
soup_can: 60
potato: 46
rubiks_cube: 16
pitcher: 14
chocolate_banana_box: 38
mug: 44
glue_stick: 37
lime: 21
toothpaste: 38
sugar_box: 20
clamp: 14
keyboard: 48
food_bag: 102
coffee_can: 18
flashlight: 18
tuna_can: 54
lego_block: 22
peach: 48
bowl: 12
shampoo_bottle: 92
wood_block: 24
banana: 54
golf_ball: 18
foam_brick: 18
jello_box: 52
tennis_ball: 14
tissue_box: 128
total_classes_with_query=52 total_query=2296


In [89]:
meta = {
    'tesla-mixture': 52,
    'tesla-unseen': 41,
    'tesla-seen': 11,
    'tesla-synthetic-seen-13': 13,
}

train_classes = 125

tfrecords_dir = f"/home/jishnu/Documents/github/meta-dataset/records-non-oversampled/{tesla_variant}/tesla"

import os, json
dataset_spec = None

with open(f"{tfrecords_dir}/dataset_spec.json", "r") as f:
    dataset_spec=json.load(f) # useful for gettings num_support values for each class


def decode(image_example):
    # Decode
    image_decoder = decoder.ImageDecoder(image_size=126)
    image_decoded = image_decoder(image_example)
    # Assert perfect reconstruction.
    with tf.Session(use_gpu=False) as sess:
        image_rec_numpy = sess.run(image_decoded)
        return image_rec_numpy

In [25]:
from meta_dataset.data import decoder
from meta_dataset.data import providers

start = train_classes
end = start + meta[tesla_variant]

image_decoder = decoder.ImageDecoder(image_size=126)
support_imgs, support_class_ids, support_labels = [], [], []
query_imgs, query_class_ids, query_labels = [], [], []
class_id_label_map = {}

for class_label, class_id in enumerate(range(start, end)):
    class_id_label_map[class_id] = class_label
    # read tfrecords to TFRecordDataset
    raw_dataset = tf.data.TFRecordDataset(f"{tfrecords_dir}/{class_id}.tfrecords")
    #  read support images
    num_support = dataset_spec['images_per_class'][str(class_id)]['support']
    
    support_class_ids.extend([class_id] * num_support)
    support_labels.extend([class_label] * num_support)
    
    for idx, ele in iterate_dataset(raw_dataset,num_support):
#         print(type(ele))
        support_image, class_id, set = image_decoder.decode_with_label_and_set(ele)
        support_imgs.extend(support_image)
#         print(idx, set)
#         break
#     break
episode = providers.Episode(
    support_imgs, support_imgs, support_labels, support_labels, support_class_ids, support_class_ids)
#     support_imgs, query_imgs, support_labels, query_labels, support_class_ids, query_class_ids)
episode.support_class_ids

[125,
 125,
 125,
 125,
 125,
 125,
 125,
 125,
 125,
 125,
 125,
 125,
 125,
 125,
 125,
 125,
 125,
 125,
 125,
 125,
 125,
 125,
 125,
 125,
 125,
 125,
 125,
 126,
 126,
 126,
 126,
 126,
 126,
 126,
 126,
 126,
 126,
 126,
 126,
 126,
 126,
 126,
 126,
 126,
 126,
 126,
 126,
 126,
 126,
 126,
 126,
 126,
 126,
 126,
 126,
 126,
 126,
 126,
 126,
 126,
 126,
 126,
 126,
 127,
 127,
 127,
 127,
 127,
 127,
 127,
 127,
 127,
 127,
 127,
 127,
 127,
 127,
 127,
 127,
 127,
 127,
 128,
 128,
 128,
 128,
 128,
 128,
 128,
 128,
 128,
 128,
 128,
 128,
 128,
 128,
 128,
 128,
 128,
 128,
 129,
 129,
 129,
 129,
 129,
 129,
 129,
 129,
 129,
 129,
 129,
 129,
 129,
 129,
 129,
 129,
 129,
 129,
 130,
 130,
 130,
 130,
 130,
 130,
 130,
 130,
 130,
 130,
 130,
 130,
 130,
 130,
 130,
 130,
 130,
 130,
 131,
 131,
 131,
 131,
 131,
 131,
 131,
 131,
 131,
 131,
 131,
 131,
 131,
 131,
 131,
 131,
 131,
 131,
 131,
 131,
 131,
 131,
 131,
 131,
 131,
 131,
 131,
 131,
 131,
 131,
 131,
 131

In [90]:
# episode.query_class_ids
# class_id_label_map

In [92]:
# ('ProtoNets', learners.PrototypicalNetworkLearner, proto_config),
from meta_dataset import trainer
from meta_dataset import learners
from meta_dataset.data import config
from meta_dataset.models import functional_backbones

ckpt_dir = 'experiment_output/tesla-unseen/checkpoints/matching_all-60-resnet34'

with tf.Session() as sess:    
    GLOBAL_STEP = 0
    #First let's load meta graph and restore weights
    saver = tf.train.import_meta_graph(f'{ckpt_dir}/model_{GLOBAL_STEP}.ckpt.meta')
    print(saver)
    saver.restore(sess, f'{ckpt_dir}/model_{GLOBAL_STEP}.ckpt')


2022-05-23 16:01:29.030135: E tensorflow/core/framework/node_def_util.cc:630] NodeDef mentions attribute validate_shape which is not in the op definition: Op<name=AssignVariableOp; signature=resource:resource, value:dtype -> ; attr=dtype:type; is_stateful=true> This may be expected if your graph generating binary is newer  than this binary. Unknown attributes will be ignored. NodeDef: {{node Adam/AssignVariableOp_21}}


INFO:tensorflow:Restoring parameters from experiment_output/tesla-unseen/checkpoints/matching_all-60-resnet34/model_0.ckpt


INFO:tensorflow:Restoring parameters from experiment_output/tesla-unseen/checkpoints/matching_all-60-resnet34/model_0.ckpt
2022-05-23 16:01:45.741136: W tensorflow/core/framework/op_kernel.cc:1745] OP_REQUIRES failed at save_restore_v2_ops.cc:207 : NOT_FOUND: Key four_layer_convnet/layer_0/batch_norm/offset not found in checkpoint


NotFoundError: Restoring from checkpoint failed. This is most likely due to a Variable name or other graph key that is missing from the checkpoint. Please ensure that you have not altered the graph expected based on the checkpoint. Original error:

Key four_layer_convnet/layer_0/batch_norm/offset not found in checkpoint
	 [[node save/RestoreV2
 (defined at /tmp/ipykernel_637103/2032731312.py:11)
]]

Errors may have originated from an input operation.
Input Source operations connected to node save/RestoreV2:
In[0] save/Const:	
In[1] save/RestoreV2/tensor_names:	
In[2] save/RestoreV2/shape_and_slices:

Operation defined at: (most recent call last)
>>>   File "/home/jishnu/anaconda3/lib/python3.9/runpy.py", line 197, in _run_module_as_main
>>>     return _run_code(code, main_globals, None,
>>> 
>>>   File "/home/jishnu/anaconda3/lib/python3.9/runpy.py", line 87, in _run_code
>>>     exec(code, run_globals)
>>> 
>>>   File "/home/jishnu/anaconda3/lib/python3.9/site-packages/ipykernel_launc

In [44]:
# 1
idx, (episode, source_id) = next(iterate_dataset(dataset_episodic, 1))
print('Got an episode from dataset:', all_dataset_specs[source_id].name)

# 2
for t, name in zip(episode,
                   ['support_images', 'support_labels', 'support_class_ids',
                    'query_images', 'query_labels', 'query_class_ids']):
  print(name, t.shape)

# 3
episode = [a.numpy() for a in episode]

# 4
support_class_ids, query_class_ids = episode[2], episode[5]
print(Counter(support_class_ids))
print(Counter(query_class_ids))
len(np.unique(query_class_ids))

NameError: name 'dataset_episodic' is not defined

In [138]:
!pip install tqdm

In [20]:
import os
import gin
import json
import numpy as np
from meta_dataset.data import decoder
from meta_dataset.data import providers
from meta_dataset.data import dataset_spec as dataset_spec_lib
from tqdm import tqdm

import tensorflow.compat.v1 as tf
tf.enable_eager_execution()


# set seed for reproducibility
seed = 1
tf.set_random_seed(seed)
np.random.seed(seed)


# dataset iterator
def iterate_dataset_n(dataset, n):
  if not tf.executing_eagerly():
    iterator = dataset.make_one_shot_iterator()
    next_element = iterator.get_next()
    with tf.Session() as sess:
      for idx in range(n):
        yield idx, sess.run(next_element)
  else:
    for idx, ele in enumerate(dataset):
      if idx == n:
        break
      yield idx, ele


# dataset iterator
def iterate_dataset(dataset):
  if not tf.executing_eagerly():
    iterator = dataset.make_one_shot_iterator()
    next_element = iterator.get_next()
    with tf.Session() as sess:
        yield idx, sess.run(next_element)
  else:
    for idx, ele in enumerate(dataset):
      yield idx, ele


meta = {
    'tesla-mixture': 52,
    'tesla-unseen': 41,
    'tesla-seen': 11,
    'tesla-synthetic-seen-13': 13,
}


GIN_FILE_PATH = 'meta_dataset/learn/gin/setups/data_config.gin'
gin.parse_config_file(GIN_FILE_PATH)


train_classes = 125
tesla_variant = list(meta.keys())[3]  # tesla-mixture
BASE_PATH = "/home/jishnu/Documents/github/meta-dataset/records-non-oversampled"
tfrecords_dir = f"{BASE_PATH}/tesla"
dataset_spec = dataset_spec_lib.load_dataset_spec(tfrecords_dir)

# Source file path
src = f"{BASE_PATH}/{tesla_variant}"

# Create a symbolic link
try:
    os.symlink(src, tfrecords_dir)
except:
    pass

start = train_classes
end = start + meta[tesla_variant]

image_decoder = decoder.ImageDecoder(image_size=126)
support_images, support_class_ids, support_labels = [], [], []
query_images, query_class_ids, query_labels = [], [], []
class_id_label_map = {}

print(f"Total classes: {meta[tesla_variant]}")
total_query_data, total_support_data = 0, 0
for class_label, class_id in enumerate(tqdm(range(start, end))):
    class_id_label_map[class_id] = class_label
    # read tfrecords to TFRecordDataset
    raw_dataset = tf.data.TFRecordDataset(
        f"{tfrecords_dir}/{class_id}.tfrecords")
    #  read support images
    num_support = dataset_spec.images_per_class[class_id]['support']
    num_query = 0
    
    for idx, example_string in iterate_dataset(raw_dataset):
        if idx < num_support:
            support_image, _, _ = \
                image_decoder.decode_with_label_and_set(example_string)
            support_images.append(support_image)
            support_class_ids.append(class_id)
            support_labels.append(class_label)
        else:
            query_image, _, _ = \
            image_decoder.decode_with_label_and_set(example_string)
            query_images.append(query_image)
            query_class_ids.append(class_id)
            query_labels.append(class_label)
            num_query += 1
    total_support_data += dataset_spec.images_per_class[class_id]['support']
    total_query_data += dataset_spec.images_per_class[class_id]['query']
    if num_query != dataset_spec.images_per_class[class_id]['query']:
        print(class_id, num_support, num_query, dataset_spec.images_per_class[class_id]['query'])
    # episode_skeleton_path = 'pkl/test.episode_skeleton.pkl'
# query_images, query_class_ids, query_labels = \
#     support_images, support_class_ids, support_labels

episode_skeleton_path = f'pkl/{tesla_variant}-episode.pkl'
episode = providers.Episode(
    support_images=support_images,
    support_class_ids=support_class_ids,
    support_labels=support_labels,
    query_images=query_images[:1026],
    query_class_ids=query_class_ids[:1026],
    query_labels=query_labels[:1026])

# print(episode)
# import pickle
# with open(episode_skeleton_path, 'wb') as pkl_file:
#     pickle.dump(episode, pkl_file)

Total classes: 13


100%|████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████| 13/13 [00:00<00:00, 13.96it/s]


In [22]:
from meta_dataset.data import decoder

# tesla-mixture
# 1025, 2294

# tesla-unseen
# 729, 1594

# tesla-seen
# 297, 700 

# tesla-unseen-synthetic-13
# 324, 140815

raw_dataset = tf.data.TFRecordDataset("support_query_records/tesla-mixture.query.tfrecords") 
for idx, example_string in iterate_dataset(raw_dataset):
    print(idx, decoder.get_class_id(example_string))

0 tf.Tensor(125, shape=(), dtype=int32)
1 tf.Tensor(125, shape=(), dtype=int32)
2 tf.Tensor(125, shape=(), dtype=int32)
3 tf.Tensor(125, shape=(), dtype=int32)
4 tf.Tensor(125, shape=(), dtype=int32)
5 tf.Tensor(125, shape=(), dtype=int32)
6 tf.Tensor(125, shape=(), dtype=int32)
7 tf.Tensor(125, shape=(), dtype=int32)
8 tf.Tensor(125, shape=(), dtype=int32)
9 tf.Tensor(125, shape=(), dtype=int32)
10 tf.Tensor(125, shape=(), dtype=int32)
11 tf.Tensor(125, shape=(), dtype=int32)
12 tf.Tensor(125, shape=(), dtype=int32)
13 tf.Tensor(125, shape=(), dtype=int32)
14 tf.Tensor(125, shape=(), dtype=int32)
15 tf.Tensor(125, shape=(), dtype=int32)
16 tf.Tensor(125, shape=(), dtype=int32)
17 tf.Tensor(125, shape=(), dtype=int32)
18 tf.Tensor(125, shape=(), dtype=int32)
19 tf.Tensor(125, shape=(), dtype=int32)
20 tf.Tensor(125, shape=(), dtype=int32)
21 tf.Tensor(125, shape=(), dtype=int32)
22 tf.Tensor(125, shape=(), dtype=int32)
23 tf.Tensor(125, shape=(), dtype=int32)
24 tf.Tensor(125, shape=()

516 tf.Tensor(133, shape=(), dtype=int32)
517 tf.Tensor(133, shape=(), dtype=int32)
518 tf.Tensor(133, shape=(), dtype=int32)
519 tf.Tensor(133, shape=(), dtype=int32)
520 tf.Tensor(133, shape=(), dtype=int32)
521 tf.Tensor(133, shape=(), dtype=int32)
522 tf.Tensor(133, shape=(), dtype=int32)
523 tf.Tensor(133, shape=(), dtype=int32)
524 tf.Tensor(133, shape=(), dtype=int32)
525 tf.Tensor(133, shape=(), dtype=int32)
526 tf.Tensor(133, shape=(), dtype=int32)
527 tf.Tensor(133, shape=(), dtype=int32)
528 tf.Tensor(133, shape=(), dtype=int32)
529 tf.Tensor(133, shape=(), dtype=int32)
530 tf.Tensor(133, shape=(), dtype=int32)
531 tf.Tensor(133, shape=(), dtype=int32)
532 tf.Tensor(133, shape=(), dtype=int32)
533 tf.Tensor(133, shape=(), dtype=int32)
534 tf.Tensor(133, shape=(), dtype=int32)
535 tf.Tensor(133, shape=(), dtype=int32)
536 tf.Tensor(133, shape=(), dtype=int32)
537 tf.Tensor(133, shape=(), dtype=int32)
538 tf.Tensor(133, shape=(), dtype=int32)
539 tf.Tensor(133, shape=(), dtype

1034 tf.Tensor(147, shape=(), dtype=int32)
1035 tf.Tensor(147, shape=(), dtype=int32)
1036 tf.Tensor(147, shape=(), dtype=int32)
1037 tf.Tensor(147, shape=(), dtype=int32)
1038 tf.Tensor(147, shape=(), dtype=int32)
1039 tf.Tensor(147, shape=(), dtype=int32)
1040 tf.Tensor(147, shape=(), dtype=int32)
1041 tf.Tensor(147, shape=(), dtype=int32)
1042 tf.Tensor(147, shape=(), dtype=int32)
1043 tf.Tensor(147, shape=(), dtype=int32)
1044 tf.Tensor(147, shape=(), dtype=int32)
1045 tf.Tensor(147, shape=(), dtype=int32)
1046 tf.Tensor(147, shape=(), dtype=int32)
1047 tf.Tensor(147, shape=(), dtype=int32)
1048 tf.Tensor(147, shape=(), dtype=int32)
1049 tf.Tensor(147, shape=(), dtype=int32)
1050 tf.Tensor(147, shape=(), dtype=int32)
1051 tf.Tensor(147, shape=(), dtype=int32)
1052 tf.Tensor(147, shape=(), dtype=int32)
1053 tf.Tensor(147, shape=(), dtype=int32)
1054 tf.Tensor(147, shape=(), dtype=int32)
1055 tf.Tensor(148, shape=(), dtype=int32)
1056 tf.Tensor(148, shape=(), dtype=int32)
1057 tf.Ten

1554 tf.Tensor(161, shape=(), dtype=int32)
1555 tf.Tensor(161, shape=(), dtype=int32)
1556 tf.Tensor(161, shape=(), dtype=int32)
1557 tf.Tensor(161, shape=(), dtype=int32)
1558 tf.Tensor(161, shape=(), dtype=int32)
1559 tf.Tensor(161, shape=(), dtype=int32)
1560 tf.Tensor(161, shape=(), dtype=int32)
1561 tf.Tensor(161, shape=(), dtype=int32)
1562 tf.Tensor(161, shape=(), dtype=int32)
1563 tf.Tensor(161, shape=(), dtype=int32)
1564 tf.Tensor(161, shape=(), dtype=int32)
1565 tf.Tensor(161, shape=(), dtype=int32)
1566 tf.Tensor(161, shape=(), dtype=int32)
1567 tf.Tensor(161, shape=(), dtype=int32)
1568 tf.Tensor(161, shape=(), dtype=int32)
1569 tf.Tensor(161, shape=(), dtype=int32)
1570 tf.Tensor(161, shape=(), dtype=int32)
1571 tf.Tensor(161, shape=(), dtype=int32)
1572 tf.Tensor(161, shape=(), dtype=int32)
1573 tf.Tensor(161, shape=(), dtype=int32)
1574 tf.Tensor(161, shape=(), dtype=int32)
1575 tf.Tensor(161, shape=(), dtype=int32)
1576 tf.Tensor(161, shape=(), dtype=int32)
1577 tf.Ten

1937 tf.Tensor(169, shape=(), dtype=int32)
1938 tf.Tensor(169, shape=(), dtype=int32)
1939 tf.Tensor(169, shape=(), dtype=int32)
1940 tf.Tensor(169, shape=(), dtype=int32)
1941 tf.Tensor(169, shape=(), dtype=int32)
1942 tf.Tensor(169, shape=(), dtype=int32)
1943 tf.Tensor(169, shape=(), dtype=int32)
1944 tf.Tensor(169, shape=(), dtype=int32)
1945 tf.Tensor(169, shape=(), dtype=int32)
1946 tf.Tensor(169, shape=(), dtype=int32)
1947 tf.Tensor(169, shape=(), dtype=int32)
1948 tf.Tensor(169, shape=(), dtype=int32)
1949 tf.Tensor(170, shape=(), dtype=int32)
1950 tf.Tensor(170, shape=(), dtype=int32)
1951 tf.Tensor(170, shape=(), dtype=int32)
1952 tf.Tensor(170, shape=(), dtype=int32)
1953 tf.Tensor(170, shape=(), dtype=int32)
1954 tf.Tensor(170, shape=(), dtype=int32)
1955 tf.Tensor(170, shape=(), dtype=int32)
1956 tf.Tensor(170, shape=(), dtype=int32)
1957 tf.Tensor(170, shape=(), dtype=int32)
1958 tf.Tensor(170, shape=(), dtype=int32)
1959 tf.Tensor(170, shape=(), dtype=int32)
1960 tf.Ten

In [38]:
raw_dataset = tf.data.TFRecordDataset("records-non-oversampled/tesla-mixture/11.tfrecords")
for idx, example_string in iterate_dataset(raw_dataset):
    print(idx, decoder.read_example_and_parse_image(example_string)['set'])

0 tf.Tensor(b'support', shape=(), dtype=string)
1 tf.Tensor(b'support', shape=(), dtype=string)
2 tf.Tensor(b'support', shape=(), dtype=string)
3 tf.Tensor(b'support', shape=(), dtype=string)
4 tf.Tensor(b'support', shape=(), dtype=string)
5 tf.Tensor(b'support', shape=(), dtype=string)
6 tf.Tensor(b'support', shape=(), dtype=string)
7 tf.Tensor(b'support', shape=(), dtype=string)
8 tf.Tensor(b'support', shape=(), dtype=string)
9 tf.Tensor(b'support', shape=(), dtype=string)
10 tf.Tensor(b'support', shape=(), dtype=string)
11 tf.Tensor(b'support', shape=(), dtype=string)
12 tf.Tensor(b'support', shape=(), dtype=string)
13 tf.Tensor(b'support', shape=(), dtype=string)
14 tf.Tensor(b'support', shape=(), dtype=string)
15 tf.Tensor(b'support', shape=(), dtype=string)
16 tf.Tensor(b'support', shape=(), dtype=string)
17 tf.Tensor(b'support', shape=(), dtype=string)
18 tf.Tensor(b'support', shape=(), dtype=string)
19 tf.Tensor(b'support', shape=(), dtype=string)
20 tf.Tensor(b'support', shape

379 tf.Tensor(b'query', shape=(), dtype=string)
380 tf.Tensor(b'query', shape=(), dtype=string)
381 tf.Tensor(b'query', shape=(), dtype=string)
382 tf.Tensor(b'query', shape=(), dtype=string)
383 tf.Tensor(b'query', shape=(), dtype=string)
384 tf.Tensor(b'query', shape=(), dtype=string)
385 tf.Tensor(b'query', shape=(), dtype=string)
386 tf.Tensor(b'query', shape=(), dtype=string)
387 tf.Tensor(b'query', shape=(), dtype=string)
388 tf.Tensor(b'query', shape=(), dtype=string)
389 tf.Tensor(b'query', shape=(), dtype=string)
390 tf.Tensor(b'query', shape=(), dtype=string)
391 tf.Tensor(b'query', shape=(), dtype=string)
392 tf.Tensor(b'query', shape=(), dtype=string)
393 tf.Tensor(b'query', shape=(), dtype=string)
394 tf.Tensor(b'query', shape=(), dtype=string)
395 tf.Tensor(b'query', shape=(), dtype=string)
396 tf.Tensor(b'query', shape=(), dtype=string)
397 tf.Tensor(b'query', shape=(), dtype=string)
398 tf.Tensor(b'query', shape=(), dtype=string)
399 tf.Tensor(b'query', shape=(), dtype=

816 tf.Tensor(b'query', shape=(), dtype=string)
817 tf.Tensor(b'query', shape=(), dtype=string)
818 tf.Tensor(b'query', shape=(), dtype=string)
819 tf.Tensor(b'query', shape=(), dtype=string)
820 tf.Tensor(b'query', shape=(), dtype=string)
821 tf.Tensor(b'query', shape=(), dtype=string)
822 tf.Tensor(b'query', shape=(), dtype=string)
823 tf.Tensor(b'query', shape=(), dtype=string)
824 tf.Tensor(b'query', shape=(), dtype=string)
825 tf.Tensor(b'query', shape=(), dtype=string)
826 tf.Tensor(b'query', shape=(), dtype=string)
827 tf.Tensor(b'query', shape=(), dtype=string)
828 tf.Tensor(b'query', shape=(), dtype=string)
829 tf.Tensor(b'query', shape=(), dtype=string)
830 tf.Tensor(b'query', shape=(), dtype=string)
831 tf.Tensor(b'query', shape=(), dtype=string)
832 tf.Tensor(b'query', shape=(), dtype=string)
833 tf.Tensor(b'query', shape=(), dtype=string)
834 tf.Tensor(b'query', shape=(), dtype=string)
835 tf.Tensor(b'query', shape=(), dtype=string)
836 tf.Tensor(b'query', shape=(), dtype=

1242 tf.Tensor(b'query', shape=(), dtype=string)
1243 tf.Tensor(b'query', shape=(), dtype=string)
1244 tf.Tensor(b'query', shape=(), dtype=string)
1245 tf.Tensor(b'query', shape=(), dtype=string)
1246 tf.Tensor(b'query', shape=(), dtype=string)
1247 tf.Tensor(b'query', shape=(), dtype=string)
1248 tf.Tensor(b'query', shape=(), dtype=string)
1249 tf.Tensor(b'query', shape=(), dtype=string)
1250 tf.Tensor(b'query', shape=(), dtype=string)
1251 tf.Tensor(b'query', shape=(), dtype=string)
1252 tf.Tensor(b'query', shape=(), dtype=string)
1253 tf.Tensor(b'query', shape=(), dtype=string)
1254 tf.Tensor(b'query', shape=(), dtype=string)
1255 tf.Tensor(b'query', shape=(), dtype=string)
1256 tf.Tensor(b'query', shape=(), dtype=string)
1257 tf.Tensor(b'query', shape=(), dtype=string)
1258 tf.Tensor(b'query', shape=(), dtype=string)
1259 tf.Tensor(b'query', shape=(), dtype=string)
1260 tf.Tensor(b'query', shape=(), dtype=string)
1261 tf.Tensor(b'query', shape=(), dtype=string)
1262 tf.Tensor(b'que

1669 tf.Tensor(b'query', shape=(), dtype=string)
1670 tf.Tensor(b'query', shape=(), dtype=string)
1671 tf.Tensor(b'query', shape=(), dtype=string)
1672 tf.Tensor(b'query', shape=(), dtype=string)
1673 tf.Tensor(b'query', shape=(), dtype=string)
1674 tf.Tensor(b'query', shape=(), dtype=string)
1675 tf.Tensor(b'query', shape=(), dtype=string)
1676 tf.Tensor(b'query', shape=(), dtype=string)
1677 tf.Tensor(b'query', shape=(), dtype=string)
1678 tf.Tensor(b'query', shape=(), dtype=string)
1679 tf.Tensor(b'query', shape=(), dtype=string)
1680 tf.Tensor(b'query', shape=(), dtype=string)
1681 tf.Tensor(b'query', shape=(), dtype=string)
1682 tf.Tensor(b'query', shape=(), dtype=string)
1683 tf.Tensor(b'query', shape=(), dtype=string)
1684 tf.Tensor(b'query', shape=(), dtype=string)
1685 tf.Tensor(b'query', shape=(), dtype=string)
1686 tf.Tensor(b'query', shape=(), dtype=string)
1687 tf.Tensor(b'query', shape=(), dtype=string)
1688 tf.Tensor(b'query', shape=(), dtype=string)
1689 tf.Tensor(b'que

...

71040 tf.Tensor(b'query', shape=(), dtype=string)
71041 tf.Tensor(b'query', shape=(), dtype=string)
71042 tf.Tensor(b'query', shape=(), dtype=string)
71043 tf.Tensor(b'query', shape=(), dtype=string)
71044 tf.Tensor(b'query', shape=(), dtype=string)
71045 tf.Tensor(b'query', shape=(), dtype=string)
71046 tf.Tensor(b'query', shape=(), dtype=string)
71047 tf.Tensor(b'query', shape=(), dtype=string)
71048 tf.Tensor(b'query', shape=(), dtype=string)
71049 tf.Tensor(b'query', shape=(), dtype=string)
71050 tf.Tensor(b'query', shape=(), dtype=string)
71051 tf.Tensor(b'query', shape=(), dtype=string)
71052 tf.Tensor(b'query', shape=(), dtype=string)
71053 tf.Tensor(b'query', shape=(), dtype=string)
71054 tf.Tensor(b'query', shape=(), dtype=string)
71055 tf.Tensor(b'query', shape=(), dtype=string)
71056 tf.Tensor(b'query', shape=(), dtype=string)
71057 tf.Tensor(b'query', shape=(), dtype=string)
71058 tf.Tensor(b'query', shape=(), dtype=string)
71059 tf.Tensor(b'query', shape=(), dtype=string)


71422 tf.Tensor(b'query', shape=(), dtype=string)
71423 tf.Tensor(b'query', shape=(), dtype=string)
71424 tf.Tensor(b'query', shape=(), dtype=string)
71425 tf.Tensor(b'query', shape=(), dtype=string)
71426 tf.Tensor(b'query', shape=(), dtype=string)
71427 tf.Tensor(b'query', shape=(), dtype=string)
71428 tf.Tensor(b'query', shape=(), dtype=string)
71429 tf.Tensor(b'query', shape=(), dtype=string)
71430 tf.Tensor(b'query', shape=(), dtype=string)
71431 tf.Tensor(b'query', shape=(), dtype=string)
71432 tf.Tensor(b'query', shape=(), dtype=string)
71433 tf.Tensor(b'query', shape=(), dtype=string)
71434 tf.Tensor(b'query', shape=(), dtype=string)
71435 tf.Tensor(b'query', shape=(), dtype=string)
71436 tf.Tensor(b'query', shape=(), dtype=string)
71437 tf.Tensor(b'query', shape=(), dtype=string)
71438 tf.Tensor(b'query', shape=(), dtype=string)
71439 tf.Tensor(b'query', shape=(), dtype=string)
71440 tf.Tensor(b'query', shape=(), dtype=string)
71441 tf.Tensor(b'query', shape=(), dtype=string)


71854 tf.Tensor(b'query', shape=(), dtype=string)
71855 tf.Tensor(b'query', shape=(), dtype=string)
71856 tf.Tensor(b'query', shape=(), dtype=string)
71857 tf.Tensor(b'query', shape=(), dtype=string)
71858 tf.Tensor(b'query', shape=(), dtype=string)
71859 tf.Tensor(b'query', shape=(), dtype=string)
71860 tf.Tensor(b'query', shape=(), dtype=string)
71861 tf.Tensor(b'query', shape=(), dtype=string)
71862 tf.Tensor(b'query', shape=(), dtype=string)
71863 tf.Tensor(b'query', shape=(), dtype=string)
71864 tf.Tensor(b'query', shape=(), dtype=string)
71865 tf.Tensor(b'query', shape=(), dtype=string)
71866 tf.Tensor(b'query', shape=(), dtype=string)
71867 tf.Tensor(b'query', shape=(), dtype=string)
71868 tf.Tensor(b'query', shape=(), dtype=string)
71869 tf.Tensor(b'query', shape=(), dtype=string)
71870 tf.Tensor(b'query', shape=(), dtype=string)
71871 tf.Tensor(b'query', shape=(), dtype=string)
71872 tf.Tensor(b'query', shape=(), dtype=string)
71873 tf.Tensor(b'query', shape=(), dtype=string)


72260 tf.Tensor(b'query', shape=(), dtype=string)
72261 tf.Tensor(b'query', shape=(), dtype=string)
72262 tf.Tensor(b'query', shape=(), dtype=string)
72263 tf.Tensor(b'query', shape=(), dtype=string)
72264 tf.Tensor(b'query', shape=(), dtype=string)
72265 tf.Tensor(b'query', shape=(), dtype=string)
72266 tf.Tensor(b'query', shape=(), dtype=string)
72267 tf.Tensor(b'query', shape=(), dtype=string)
72268 tf.Tensor(b'query', shape=(), dtype=string)
72269 tf.Tensor(b'query', shape=(), dtype=string)
72270 tf.Tensor(b'query', shape=(), dtype=string)
72271 tf.Tensor(b'query', shape=(), dtype=string)
72272 tf.Tensor(b'query', shape=(), dtype=string)
72273 tf.Tensor(b'query', shape=(), dtype=string)
72274 tf.Tensor(b'query', shape=(), dtype=string)
72275 tf.Tensor(b'query', shape=(), dtype=string)
72276 tf.Tensor(b'query', shape=(), dtype=string)
72277 tf.Tensor(b'query', shape=(), dtype=string)
72278 tf.Tensor(b'query', shape=(), dtype=string)
72279 tf.Tensor(b'query', shape=(), dtype=string)


72687 tf.Tensor(b'query', shape=(), dtype=string)
72688 tf.Tensor(b'query', shape=(), dtype=string)
72689 tf.Tensor(b'query', shape=(), dtype=string)
72690 tf.Tensor(b'query', shape=(), dtype=string)
72691 tf.Tensor(b'query', shape=(), dtype=string)
72692 tf.Tensor(b'query', shape=(), dtype=string)
72693 tf.Tensor(b'query', shape=(), dtype=string)
72694 tf.Tensor(b'query', shape=(), dtype=string)
72695 tf.Tensor(b'query', shape=(), dtype=string)
72696 tf.Tensor(b'query', shape=(), dtype=string)
72697 tf.Tensor(b'query', shape=(), dtype=string)
72698 tf.Tensor(b'query', shape=(), dtype=string)
72699 tf.Tensor(b'query', shape=(), dtype=string)
72700 tf.Tensor(b'query', shape=(), dtype=string)
72701 tf.Tensor(b'query', shape=(), dtype=string)
72702 tf.Tensor(b'query', shape=(), dtype=string)
72703 tf.Tensor(b'query', shape=(), dtype=string)
72704 tf.Tensor(b'query', shape=(), dtype=string)
72705 tf.Tensor(b'query', shape=(), dtype=string)
72706 tf.Tensor(b'query', shape=(), dtype=string)


In [76]:
with open(episode_skeleton_path, 'rb') as pkl_file:
    c = pickle.load(pkl_file)
    b=c
#     print(b)

In [77]:
total_query_data, len(b.query_class_ids), len(b.query_labels), len(b.query_images)

(2296, 2294, 2294, 2294)

In [78]:
total_support_data, len(b.support_class_ids), len(b.support_labels), len(b.support_images)

(1026, 1026, 1026, 1026)

In [79]:
for i,j in zip(b.support_class_ids, b.support_labels):
    print(i,j)

125 0
125 0
125 0
125 0
125 0
125 0
125 0
125 0
125 0
125 0
125 0
125 0
125 0
125 0
125 0
125 0
125 0
125 0
125 0
125 0
125 0
125 0
125 0
125 0
125 0
125 0
125 0
126 1
126 1
126 1
126 1
126 1
126 1
126 1
126 1
126 1
126 1
126 1
126 1
126 1
126 1
126 1
126 1
126 1
126 1
126 1
126 1
126 1
126 1
126 1
126 1
126 1
126 1
126 1
126 1
126 1
126 1
126 1
126 1
126 1
126 1
126 1
126 1
127 2
127 2
127 2
127 2
127 2
127 2
127 2
127 2
127 2
127 2
127 2
127 2
127 2
127 2
127 2
127 2
127 2
127 2
128 3
128 3
128 3
128 3
128 3
128 3
128 3
128 3
128 3
128 3
128 3
128 3
128 3
128 3
128 3
128 3
128 3
128 3
129 4
129 4
129 4
129 4
129 4
129 4
129 4
129 4
129 4
129 4
129 4
129 4
129 4
129 4
129 4
129 4
129 4
129 4
130 5
130 5
130 5
130 5
130 5
130 5
130 5
130 5
130 5
130 5
130 5
130 5
130 5
130 5
130 5
130 5
130 5
130 5
131 6
131 6
131 6
131 6
131 6
131 6
131 6
131 6
131 6
131 6
131 6
131 6
131 6
131 6
131 6
131 6
131 6
131 6
131 6
131 6
131 6
131 6
131 6
131 6
131 6
131 6
131 6
131 6
131 6
131 6
131 6
131 